In [1]:
import sys
if ".." not in sys.path:
    sys.path.insert(0, "..")

In [9]:
import os
from datetime import date, timedelta
import pandas as pd
import numpy as np
from information.terms_info import tags

pd.set_option('display.max_columns', None)
print(f'{tags}')

['flu', 'cough', 'fever', 'headache', 'lagnat', 'rashes', 'sipon', 'ubo', 'ecq', 'face-shield', 'Frontliners', 'masks', 'Quarantine', 'social-distancing', 'work-from-home']


In [3]:
"""
 Declare data scope
"""
# start_date = date.fromisoformat('2020-01-01')
start_date = date.fromisoformat('2020-03-16')
end_date   = date.fromisoformat('2021-02-15')

end_dates = []
current_date = start_date
while (current_date <= end_date):
    end_dates.append(str(current_date).replace('-', ' '))
    current_date += timedelta(days=1)
print(f"{len(end_dates)=}")

len(end_dates)=337


In [11]:
# ... existing code ...
for tag in tags:
    normalize_tag = tag.replace('/', '.')
    msv_df_csv_path = os.path.abspath(f'./../msvs/processed/{normalize_tag}.csv')
    msv_df_pkl_path = os.path.abspath(f'./../msvs/processed/{normalize_tag}.pkl')

    msv_df = None

    for current_date in end_dates:
        current_rsv_path = os.path.join(r"C:\Users\Cheska\Documents\GitHub\-Thesis-Infodemiology-GT\covid-19-google-trends-network\scripts\msvs\data", normalize_tag, f"{current_date}.csv")
        rsv_df = pd.read_csv(current_rsv_path, parse_dates=['date'])
        rsv_df.drop(columns=['isPartial'], inplace=True)
        rsv_df.columns = ['date', 'index']

        if msv_df is None:
            msv_df = rsv_df.copy()
        else:
            # Join data into one
            merged_df = msv_df.merge(rsv_df, on='date', how='outer')

            # Calculate correction factors
            merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
            merged_df['correction_factor'] = merged_df['correction_factor'].fillna(1)
            merged_df['correction_factor'] = merged_df['correction_factor'].replace([np.inf, -np.inf], np.nan)
            aggregated_correction_factor = merged_df['correction_factor'].mean()

            # Rescale the new RSV
            merged_df['index_y'] = merged_df['index_y'] * aggregated_correction_factor

            # Fill new data into previous RSV/MSV
            merged_df['index_x'] = merged_df['index_x'].fillna(merged_df['index_y'])
            print(merged_df.tail())
            
            msv_df = merged_df[['date', 'index_x']].copy()
            msv_df.columns = ['date', 'index']

        print(rsv_df.describe())
        
    msv_df.to_csv(msv_df_csv_path, index=False)
    msv_df.to_pickle(msv_df_pkl_path)

# ... rest of the code ...

                      date       index
count                   31   31.000000
mean   2020-03-31 00:00:00   25.612903
min    2020-03-16 00:00:00   12.000000
25%    2020-03-23 12:00:00   15.500000
50%    2020-03-31 00:00:00   21.000000
75%    2020-04-07 12:00:00   31.000000
max    2020-04-15 00:00:00  100.000000
std                    NaN   16.819983
         date    index_x    index_y  correction_factor
27 2020-04-12  12.000000  48.746135           2.083333
28 2020-04-13  15.000000  58.495362           2.000000
29 2020-04-14  13.000000  50.695980           2.000000
30 2020-04-15  13.000000  52.645826           2.076923
31 2020-04-16  37.047062  37.047062           1.000000
                      date       index
count                   31   31.000000
mean   2020-04-01 00:00:00   45.645161
min    2020-03-17 00:00:00   19.000000
25%    2020-03-24 12:00:00   30.500000
50%    2020-04-01 00:00:00   41.000000
75%    2020-04-08 12:00:00   56.000000
max    2020-04-16 00:00:00  100.000000
std    

C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor

         date    index_x   index_y  correction_factor
40 2020-04-25   0.000000  66.00788                NaN
41 2020-04-26  67.432351   0.00000                0.0
42 2020-04-27   0.000000   0.00000                1.0
43 2020-04-28   0.000000   0.00000                1.0
44 2020-04-29   0.000000   0.00000                1.0
                      date       index
count                   31   31.000000
mean   2020-04-14 00:00:00   27.838710
min    2020-03-30 00:00:00    0.000000
25%    2020-04-06 12:00:00    0.000000
50%    2020-04-14 00:00:00    0.000000
75%    2020-04-21 12:00:00   62.500000
max    2020-04-29 00:00:00  100.000000
std                    NaN   36.497577
         date    index_x    index_y  correction_factor
41 2020-04-26  67.432351   0.000000                0.0
42 2020-04-27   0.000000   0.000000                1.0
43 2020-04-28   0.000000   0.000000                1.0
44 2020-04-29   0.000000   0.000000                1.0
45 2020-04-30  70.619527  70.619527               

C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor

         date  index_x  index_y  correction_factor
55 2020-05-10      0.0      0.0                1.0
56 2020-05-11      0.0      0.0                1.0
57 2020-05-12      0.0      0.0                1.0
58 2020-05-13      0.0      0.0                1.0
59 2020-05-14      0.0      0.0                1.0
                      date       index
count                   31   31.000000
mean   2020-04-29 00:00:00   17.000000
min    2020-04-14 00:00:00    0.000000
25%    2020-04-21 12:00:00    0.000000
50%    2020-04-29 00:00:00    0.000000
75%    2020-05-06 12:00:00    0.000000
max    2020-05-14 00:00:00  100.000000
std                    NaN   32.602658
         date  index_x    index_y  correction_factor
56 2020-05-11      0.0   0.000000                1.0
57 2020-05-12      0.0   0.000000                1.0
58 2020-05-13      0.0   0.000000                1.0
59 2020-05-14      0.0  65.400571                NaN
60 2020-05-15      0.0   0.000000                1.0
                      dat

...

C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] 

          date    index_x    index_y  correction_factor
332 2021-02-11  56.817759  56.904956           1.003207
333 2021-02-12  46.868114  46.921631           1.002814
334 2021-02-13  53.869122  53.909959           1.002430
335 2021-02-14   0.000000   0.000000           1.000000
336 2021-02-15  41.929968  41.929968           1.000000
                      date       index
count                   31   31.000000
mean   2021-01-31 00:00:00   58.548387
min    2021-01-16 00:00:00    0.000000
25%    2021-01-23 12:00:00   46.500000
50%    2021-01-31 00:00:00   64.000000
75%    2021-02-07 12:00:00   76.000000
max    2021-02-15 00:00:00  100.000000
std                    NaN   25.130113
          date    index_x    index_y  correction_factor
333 2021-02-12  46.868114  46.922095           1.002814
334 2021-02-13  53.869122  53.910492           1.002430
335 2021-02-14   0.000000   0.000000           1.000000
336 2021-02-15  41.929968  41.930383           1.001670
337 2021-02-16  68.885628  68.885

C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'

                      date       index
count                   31   31.000000
mean   2021-02-12 00:00:00   61.161290
min    2021-01-28 00:00:00    0.000000
25%    2021-02-04 12:00:00   52.500000
50%    2021-02-12 00:00:00   66.000000
75%    2021-02-19 12:00:00   83.500000
max    2021-02-27 00:00:00  100.000000
std                    NaN   30.760469
          date     index_x     index_y  correction_factor
345 2021-02-24   92.717516   73.328803           0.787338
346 2021-02-25   97.846414   76.342316           0.776727
347 2021-02-26   64.719587   59.265745           0.911625
348 2021-02-27    0.000000   42.189174                NaN
349 2021-02-28  100.450415  100.450415           1.000000
                      date       index
count                   31   31.000000
mean   2021-02-13 00:00:00   62.000000
min    2021-01-29 00:00:00    0.000000
25%    2021-02-05 12:00:00   50.500000
50%    2021-02-13 00:00:00   67.000000
75%    2021-02-20 12:00:00   81.000000
max    2021-02-28 00:00:00  

C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: invalid value encountered in divide
  merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
C:\Users\Cheska\AppData\Local\Temp\ipykernel_9512\612270428.py:22: RuntimeWarning: divide by zero encountered in divide
  merged_df['correction_factor

In [10]:
for tag in tags:
    normalize_tag = tag.replace('/', '.')
    #rsv_directory = os.path.abspath()
    msv_df_csv_path = os.path.abspath(f'./../msvs/processed/{normalize_tag}.csv')
    msv_df_pkl_path = os.path.abspath(f'./../msvs/processed/{normalize_tag}.pkl')

    msv_df = None

    for current_date in end_dates:
        current_rsv_path = os.path.join("C:\\Users\\Cheska Hung\\Desktop\\Thesis-GT Infodemiology\\-Thesis-Infodemiology-GT\\covid-19-google-trends-network\\scripts\\msvs\\data", normalize_tag, f"{current_date}.csv")
        rsv_df = pd.read_csv(current_rsv_path, parse_dates=['date'])
        rsv_df.drop(columns=['isPartial'], inplace=True)
        rsv_df.columns = ['date', 'index']

        if msv_df is None:
            msv_df = rsv_df.copy()
        else:
            # Join data into one
            merged_df = msv_df.merge(rsv_df, on='date', how='outer')

            # Calculate correction factors
            merged_df['correction_factor'] = merged_df['index_y'].values / merged_df['index_x'].values
            merged_df['correction_factor'] = merged_df['correction_factor'].fillna(1)
            merged_df['correction_factor'] = merged_df['correction_factor'].round(4)
            aggregated_correction_factor = merged_df['correction_factor'].mean()

            # Resclae the new RSV
            merged_df['index_y'] = merged_df['index_y'] * aggregated_correction_factor

            # Fill new data into previous RSV/MSV
            merged_df['index_x'] = merged_df['index_x'].fillna(merged_df['index_y'])
            print(merged_df.tail())
            
            msv_df = merged_df[['date', 'index_x']].copy()
            msv_df.columns = ['date', 'index']

        print(rsv_df.describe())
        
    msv_df.to_csv(msv_df_csv_path, index=False)
    msv_df.to_pickle(msv_df_pkl_path)

FileNotFoundError: [Errno 2] No such file or directory: 'C:\\Users\\Cheska Hung\\Desktop\\Thesis-GT Infodemiology\\-Thesis-Infodemiology-GT\\covid-19-google-trends-network\\scripts\\msvs\\data\\flu\\2020 03 16.csv'